# Assignment 5: Anomaly Detection

## Objective

In this assignment, you will be instructed to apply **unsupervised** learning to address a practical problem. For simplicity, we will use intrusion detection as an example. But the principle can be used in many other fields, such as fraud detection and medical care. After completing this assignment, you should be able to answer the following questions:

1. How to standardize numerical features?
2. How to transform categorical features into numerical features?
3. How to derive anomalies from clustering results?
4. How to tune parameters for unsupervised learning?

The data can be downloaded from [A5-data.zip](https://coursys.sfu.ca/2024sp-cmpt-733-g1/pages/A5-data).

### Overview

In practice, when you are facing an ML problem, the process of solving it basically consists of two phases: _model development_ and _model serving_. 

* In model development, your job is to figure out what's the best algorithms, features, and parameters should be chosen based on historical data. This is often an iterative and off-line process. 

* Once you develop a satisfactory model, you will need to use the model to serve new requests and make predictions. This is often an on-line process, so you have to think about how to make the predictions as fast as possible and how to efficiently update the model when new data arrive. 

In this assignment, you are going to focus on the model development stage. Model serving is also a very important topic. I hope you can learn it by yourself or through your final project. Below are a few good references: 
* [Deploy a Model in Amazon SageMaker](https://docs.aws.amazon.com/sagemaker/latest/dg/how-it-works-deployment.html)
* [TensorFlow Serving](https://www.tensorflow.org/tfx/guide/serving)
* [Deploy models with Azure Machine Learning](https://docs.microsoft.com/en-us/azure/machine-learning/how-to-deploy-and-where)
* [Serving of ML models in Kubeflow](https://www.kubeflow.org/docs/external-add-ons/serving/)
* [MLflow Model Serving on Databricks](https://docs.databricks.com/applications/mlflow/model-serving.html)

### Model Development

Suppose you want to develop a model that can detect anomalous connections to your company's server. The server log contains all the information of historical connections; your nice colleague has already helped you to transform the raw log into a collection of feature vectors, where each feature vector characterizes a connection in 40 dimensions, e.g., number of failed login attempts, length (number of seconds) of the connection. Here is one example feature vector:
```
[udp,SF,0,105,146,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,1,1,0.00,0.00,0.00,0.00,1.00,0.00,0.00,255,240,0.94,0.01,0.00,0.00,0.00,0.00,0.00,0.00]
```

Your task is to take these feature vectors as input and develop an unsupervised-learning model to detect anomalous connections. In the lecture, we have gone through this process. In the assignment, you are going to implement three functions: `cat2Num`, `scaleNum`, and `detect`, by doing Tasks A-C, respectively.

``` python
# anomaly_detection.py
import pandas as pd


class AnomalyDetection():
    
    def scaleNum(self, df, indices):
        """
            Write your code!
        """
    
    
    def cat2Num(self, df, indices):
        """
            Write your code!
        """
            

    def detect(self, df, k, t):
        """
            Write your code!
        """
        
    
 
if __name__ == "__main__":
    df = pd.read_csv('logs-features-sample.csv').set_index('id')
    ad = AnomalyDetection()
    
    df1 = ad.cat2Num(df, [0,1])
    print(df1)

    df2 = ad.scaleNum(df1, [6])
    print(df2)

    df3 = ad.detect(df2, 8, 0.97)
    print(df3)
```

### A toy dataset for testing

To test your program, you can read a toy dataset:

```python
    data = [(0, ["http", "udt", 4]), \
            (1, ["http", "udf", 5]), \
            (2, ["http", "tcp", 5]), \
            (3, ["ftp", "icmp", 1]), \
            (4, ["http", "tcp", 4])]

    df = pd.DataFrame(data=data, columns = ["id", "features"])
        
```

After running the script, your program should output the followings:

**df1 = ad.cat2Num(df, [0,1])**

```
+---+---------------------+
|id |features             |
+---+---------------------+
|0  |[1, 0, 1, 0, 0, 0, 4]|
|1  |[1, 0, 0, 1, 0, 0, 5]|
|2  |[1, 0, 0, 0, 1, 0, 5]|
|3  |[0, 1, 0, 0, 0, 1, 1]|
|4  |[1, 0, 0, 0, 1, 0, 4]|
+---+---------------------+
```

**df2 = ad.scaleNum(df1, [6]):**

```
+---+---------------------------------------+
|id |features                               |
+---+---------------------------------------+
|0  |[1, 0, 1, 0, 0, 0, 0.12171612389003701]|
|1  |[1, 0, 0, 1, 0, 0, 0.7302967433402214] |
|2  |[1, 0, 0, 0, 1, 0, 0.7302967433402214] |
|3  |[0, 1, 0, 0, 0, 1, -1.704025734460517] |
|4  |[1, 0, 0, 0, 1, 0, 0.12171612389003701]|
+---+---------------------------------------+
```

**df3 = ad.detect(df2, 2, 0.9)**

```
+---+---------------------------------------+-----+
|id |features                               |score|
+---+---------------------------------------+-----+
|3  |[0, 1, 0, 0, 0, 1, -1.704025734460517] |1.0  |
+---+----------------+----------------------+-----+
```

### Task A. Categorical Features --> Numerical Features

As you can see from the above feature vector, the first two dimensions in each feature vector are categorical features. For example, the first dimension can be one of the following cases: “http” or “ftp”. You can represent these categorical features using one-hot encoding, e.g., [1,0] for “http” and [0,1] for “ftp”. 

In Task A, your job is to implement the `cat2Num` function.

```python
    def cat2Num(self, df, indices):
        """ 
            Input: $df represents a DataFrame with two columns: "id" and "features"
                   $indices represents which dimensions in $features are categorical features, 
                    e.g., indices = [0, 1] denotes that the first two dimensions are categorical features.
                    
            Output: Return a new DataFrame that updates the "features" column with one-hot encoding. 
            
        """
    
```

**Note**: You have to implement one-hot encoding by yourself rather than use an existing implmentation in a libary. 


In [1]:
import pandas as pd

### Task B. Standardize Numerical Features 

K-Means utilizes the distance between every two points to do clustering. We don't want the distance to be dominated by some features. To avoid this, we standardize those features that are on a larger scale. 

In Task B, your job is to implement the `scaleNum` function, which standardizes specified features by removing the mean and scaling to unit variance.


```python
    def scaleNum(self, df, indices):
        """ 
            Input: $df represents a DataFrame with two columns: "id" and "features"
                   $indices represents which dimensions in $features that need to be standardized
                    
            Output: Return a new DataFrame that updates "features" column with specified features standarized.
            
        """
    
```

**Note:** You have to implement StandardScaler by yourself rather than use an existing implmentation in a libary

In [140]:
data = [(0, ["http", "udt", 4]), \
            (1, ["http", "udf", 5]), \
            (2, ["http", "tcp", 5]), \
            (3, ["ftp", "icmp", 1]), \
            (4, ["http", "tcp", 4])]

df = pd.DataFrame(data=data, columns = ["id", "features"])
# print(df)

# Task A 
indices = [0, 1]

features_df = df['features'].apply(pd.Series)

for i in sorted(indices, reverse=True):    
    fea = features_df.iloc[:, i]
    col_names = fea.unique()
    fea_df = pd.DataFrame()
    for col in col_names:
        fea_df[col] = (fea == col).astype(int)
    features_df = pd.concat([features_df.iloc[:, :i], fea_df, features_df.iloc[:, i+1:]], axis=1)
    
df['features'] = features_df.apply(lambda row: row.tolist(), axis=1)
print(df)

# print('-' * 50)
# Task B
indices = [6]

features_df = df['features'].apply(pd.Series)
for i in indices:    
    fea = features_df.iloc[:, i]
    fea_mean = fea.mean()
    fea_std = fea.std()
    for row in df['features']:
        row[i] = (row[i] - fea_mean) / fea_std
    
print(df)

   id               features
0   0  [1, 0, 1, 0, 0, 0, 4]
1   1  [1, 0, 0, 1, 0, 0, 5]
2   2  [1, 0, 0, 0, 1, 0, 5]
3   3  [0, 1, 0, 0, 0, 1, 1]
4   4  [1, 0, 0, 0, 1, 0, 4]
   id                                 features
0   0  [1, 0, 1, 0, 0, 0, 0.12171612389003701]
1   1   [1, 0, 0, 1, 0, 0, 0.7302967433402215]
2   2   [1, 0, 0, 0, 1, 0, 0.7302967433402215]
3   3  [0, 1, 0, 0, 0, 1, -1.7040257344605165]
4   4  [1, 0, 0, 0, 1, 0, 0.12171612389003701]


In [141]:
type(df['features'][0])

list

In [131]:
df['features']

0    [1, 0, 1, 0, 0, 0, 0.12171612389003701]
1     [1, 0, 0, 1, 0, 0, 0.7302967433402215]
2     [1, 0, 0, 0, 1, 0, 0.7302967433402215]
3    [0, 1, 0, 0, 0, 1, -1.7040257344605165]
4    [1, 0, 0, 0, 1, 0, 0.12171612389003701]
Name: features, dtype: object

### Task C. Detect Anomalies

As you may remember, the intuition of our anomaly detection approach was that clusters with a small number of data points will correspond to attacks or anomalies. We use this intuition to generate a confidence score from the clustering model’s output. The confidence score reflects how much the clustering model believes a data point is an attack or not. Let us assume $x$ is a data point describing a network connection. We can use:

$$score(x) = \frac{N_{max}-N_{x}}{N_{max}-N_{min}}$$

to score $x$ as being an anomaly. Note that in this equation, $N_{max}$ and $N_{min}$ reflect the size of the largest and smallest clusters, respectively. $N_{x}$ represents the size of the cluster assigned to $x$. If you check the equation carefully, you will notice that $score(x) = 1$ when $x$ is assigned to the smallest cluster and $score(x)$ = 0 when $x$ is assigned to a large cluster.


In Task C, your job is to implement the `detect` function. 

```python
def detect(self, df, k, t):
    """ 
        Input: $df represents a DataFrame with two columns: "id" and "features"
               $k is the number of clusters for K-Means
               $t is the score threshold
        
        Output: Return a new DataFrame that adds the "score" column into the input $df and then
                removes the rows whose scores are smaller than $t.  
    """
```

In [112]:
from sklearn.cluster import KMeans
import numpy as np

k = 3
t = 0.8

X = np.array(df['features'].tolist())
kmeans = KMeans(n_clusters=3)
kmeans.fit(X)
df['labels'] = kmeans.labels_

label_stat = df['labels'].value_counts().reset_index()
label_stat.columns = ['labels', 'n']
n_max = label_stat['n'].max()
n_min = label_stat['n'].min()
label_stat['score'] = (n_max - label_stat['n']) / (n_max - n_min)
df = df.merge(label_stat, on='labels').drop(columns=['labels', 'n'])

# df
df[df['score'] >= t]

id                                 features  score
4   3  [0, 1, 0, 0, 0, 1, -1.7040257344605165]    1.0

In [147]:
df = pd.read_csv('logs-features-sample.csv')
df.columns

Index(['id', 'features'], dtype='object')

In [154]:
df['features'] = df['features'].str.replace('[', '').str.replace(']', '').apply(lambda x: x.split(','))
df

/var/folders/cl/j9k2b3n537bg1fr81hb9b5jh0000gn/T/ipykernel_90478/1683118900.py:1: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.
  df['features'] = df['features'].str.replace('[', '').str.replace(']', '').apply(lambda x: x.split(','))


id                                           features
0          0  ['tcp',  'SF',  -0.157817888091,  0.0156775057...
1          1  ['tcp',  'SF',  -0.158545578037,  -0.028258192...
2          2  ['tcp',  'SF',  -0.158545578037,  -0.026147460...
3          3  ['tcp',  'SF',  -0.158545578037,  0.0132420457...
4          4  ['udp',  'SF',  -0.158545578037,  -0.031440527...
...      ...                                                ...
99090  99090  ['tcp',  'SF',  -0.158545578037,  -0.024004255...
99091  99091  ['udp',  'SF',  1.7552789774,  -0.030109142279...
99092  99092  ['tcp',  'SF',  -0.158545578037,  -0.029654523...
99093  99093  ['tcp',  'S0',  -0.158545578037,  -0.034850171...
99094  99094  ['tcp',  'SF',  -0.158545578037,  -0.026244879...

[99095 rows x 2 columns]

In [158]:
df.shape

(99095, 2)

In [159]:
# Task A 
indices = [0, 1]
df1 = df.copy()
features_df = df1['features'].apply(pd.Series)

for i in sorted(indices, reverse=True):    
    fea = features_df.iloc[:, i]
    col_names = fea.unique()
    fea_df = pd.DataFrame()
    for col in col_names:
        fea_df[col] = (fea == col).astype(int)
    features_df = pd.concat([features_df.iloc[:, :i], fea_df, features_df.iloc[:, i+1:]], axis=1)
    
df1['features'] = features_df.apply(lambda row: row.tolist(), axis=1)
print(df1.head())

   id                                           features
0   0  [1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0,  -0.15781...
1   1  [1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0,  -0.15854...
2   2  [1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0,  -0.15854...
3   3  [1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0,  -0.15854...
4   4  [0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0,  -0.15854...


In [164]:
indices = list(range(len(df1['features'][0]) - len(df['features'][0]) + 2, len(df1['features'][0])))
df2 = df1.copy()
features_df = df2['features'].apply(pd.Series)
# selected_features = features_df.iloc[:, indices]
# means = selected_features.mean()
# stds = selected_features.std()
# features_df.iloc[:, indices] = (selected_features - means) / stds

features_df.head()

0   1   2   3   4   5   6   7   8   9   ...               40  \
0   1   0   0   1   0   0   0   0   0   0  ...   -1.08520379254   
1   1   0   0   1   0   0   0   0   0   0  ...    1.01148104848   
2   1   0   0   1   0   0   0   0   0   0  ...   -1.12385236104   
3   1   0   0   1   0   0   0   0   0   0  ...   -1.02723093979   
4   0   1   0   1   0   0   0   0   0   0  ...    1.01148104848   

                 41                 42                43                44  \
0   -0.670692144755     -2.13752170679    0.134610448419   -0.390669630719   
1    0.608141013824     0.509691253801   -0.313427922094   -0.491495247329   
2    0.608141013824     0.509691253801   -0.313427922094   -0.390669630719   
3   -0.111202637877   -0.0714042741323   0.0786056521051   -0.424278169589   
4    0.414032409397     0.283709659605    -0.25742312578   -0.491495247329   

                 45                 46                 47                48  \
0   -0.276444957812   -0.0898125413262    0.0651434083328   -0.255026418809   
1   -0.476202232196   -0.0898125413262   -0.0806915865556   -0.210441191777   
2    0.922098688489     0.323121796479   -0.0806915865556   -0.255026418809   
3   -0.276444957812   -0.0898125413262    0.0651434083328   -0.255026418809   
4   -0.476202232196   -0.0898125413262   -0.0806915865556   -0.255026418809   

                 49  
0   -0.254165764143  
1   -0.208336861971  
2   -0.254165764143  
3   -0.254165764143  
4   -0.254165764143  

[5 rows x 50 columns]

In [167]:
features_df.iloc[:, 12].mean()

TypeError: Could not convert  -0.157817888091 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 1.46420299939 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.154179438366 -0.158545578037 -0.147630228861 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.141808709301 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 2.89556912127 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.158545578037 -0.15781788809

In [122]:
# Task A 
indices = [0, 1]

features_df = df['features'].apply(pd.Series)

for i in sorted(indices, reverse=True):
    print(i)    
    fea = features_df.iloc[:, i]
    col_names = fea.unique()
    fea_df = pd.DataFrame()
    for col in col_names:
        fea_df[col] = (fea == col).astype(int)
    features_df = pd.concat([features_df.iloc[:, :i], fea_df, features_df.iloc[:, i+1:]], axis=1)
    
df['features'] = features_df.apply(lambda row: row.tolist(), axis=1)
print(df.head())

1


IndexError: single positional indexer is out-of-bounds

### Task D. Hyperparameter Tuning

Hyperparameter tuning plays an essential role in improving model quality. In this assignment, your task is to figure out how to tune hyperparameters for **unsupervised learning**. There are two parameters that need to be tuned: 

* $k$: the number of clusters
* $t$: the score threshold 

They are set to k = 8 and t = 0.97 in the above program. In fact, if you changed them to different values, the result could be quite different. Thus, it is important to know how to tune $k$ and $t$ in practice.  

In Task D, imagine you are a data science manager. Please write an email (< 500 words) to tell a junior data scientist (named Nick) how to use [Bayesian Optimization](http://krasserm.github.io/2018/03/21/bayesian-optimization/) to tune the parameters. Your email needs to explain to Nick i) how bayesian optimization works in an intuitive way, and ii) why bayesian optimization could perform better than grid search and random search.


## Submission

Implement `cat2Num`, `scaleNum`, and `detect` functions in `anomaly_detection.py`. Submit your code file (`anomaly_detection.py`), and your email content (`email.pdf`) to CourSys.